In [2]:
import json
with open('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/author_nodes.json', 'r') as file:
    author_nodes = json.load(file)
len(author_nodes)

35751

In [1]:
import json
with open('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/venue_nodes.json', 'r') as file:
    venue_nodes = json.load(file)
len(venue_nodes)

14111

In [4]:
import json
with open('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/mesh_nodes.json', 'r') as file:
    mesh_nodes = json.load(file)
len(mesh_nodes)

28338

In [3]:
import json
with open('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/paper_nodes.json', 'r') as file:
    paper_nodes = json.load(file)
len(paper_nodes)

1792034

# gen a small dataset for efficient (only consider core papers)

In [4]:
core_paper_nodes = {}
for k,v in paper_nodes.items():
    if v['features']['is_core'] == 1:
        core_paper_nodes[k] = v

In [91]:
core_paper_set = set(core_paper_nodes.keys())

In [92]:
from tqdm import tqdm
for k in tqdm(core_paper_nodes):
    core_paper_nodes[k]['neighbors']['citing_papers'] = list(set(core_paper_nodes[k]['neighbors']['citing_papers']) &  core_paper_set)
    core_paper_nodes[k]['neighbors']['reference_papers'] = list(set(core_paper_nodes[k]['neighbors']['reference_papers']) &  core_paper_set)

100%|██████████| 12065/12065 [00:00<00:00, 111638.99it/s]


In [93]:
len(core_paper_nodes)

12065

In [12]:
# Dictionaries to store the mappings with paper_id in their names
old_paper_id_to_new_map = {}
new_paper_id_to_old_map = {}

# Iterate over the dictionary and create the mappings
for new_paper_id, old_paper_id in enumerate(core_paper_nodes):
    old_paper_id_to_new_map[old_paper_id] = new_paper_id
    new_paper_id_to_old_map[new_paper_id] = old_paper_id

# Create the new dictionary with the new keys
new_core_paper_nodes = {new_paper_id: core_paper_nodes[old_paper_id] for old_paper_id, new_paper_id in old_paper_id_to_new_map.items()}

In [6]:
del paper_nodes

In [95]:
old_author_id_to_new_map = {}
new_author_id_to_old_map = {}

# Iterate over the dictionary and create the mappings
for new_author_id, old_author_id in enumerate(author_nodes):
    old_author_id_to_new_map[old_author_id] = new_author_id
    new_author_id_to_old_map[new_author_id] = old_author_id

# Create the new dictionary with the new keys
new_author_nodes = {new_author_id: author_nodes[old_author_id] for old_author_id, new_author_id in old_author_id_to_new_map.items()}

Let's Create!

In [96]:
import dgl
import torch

In [105]:
data_dict = {
    ('author', 'author-paper', 'paper'): (torch.tensor(author_write_paper_author), torch.tensor(author_write_paper_paper)),
    ('paper', 'cite', 'paper'): (torch.tensor(paper_cite_reference_paper), torch.tensor(paper_cite_reference_reference)),
    ('paper', 'paper-author', 'author'): (torch.tensor(author_write_paper_paper), torch.tensor(author_write_paper_author)),
    ('paper', 'paper-venue', 'venue'): (torch.tensor(paper_venue_paper_paper), torch.tensor(paper_venue_paper_venue)),
    ('venue', 'venue-paper', 'paper'):(torch.tensor(paper_venue_paper_venue), torch.tensor(paper_venue_paper_paper)),
}

In [98]:
author_write_paper_author = []
author_write_paper_paper = []
for k,v in new_core_paper_nodes.items():
    for old_author_id in v['neighbors']['author'].keys():
        author_write_paper_paper.append(k)
        author_write_paper_author.append(old_author_id_to_new_map[old_author_id])

In [99]:
paper_cite_reference_paper = []
paper_cite_reference_reference = []
for k,v in new_core_paper_nodes.items():
    if len(v['neighbors']['reference_papers']) != 0:
        for old_paper_id in v['neighbors']['reference_papers']:
            paper_cite_reference_paper.append(k)
            paper_cite_reference_reference.append(old_paper_id_to_new_map[old_paper_id])

In [108]:
venue_set = set()
venue_set.update(['Lancet (London, England)'])
venue_set

{'Lancet (London, England)'}

In [109]:
venue_set = set()
for k,v in new_core_paper_nodes.items():
    venue_set.update([v['features']['Venue']])

In [112]:
venue_list = list(venue_set)
old_venue_id_to_new_map = {}
new_venue_id_to_old_map = {}

# Iterate over the list and create the mappings
for new_venue_id, old_venue_id in enumerate(venue_list):
    old_venue_id_to_new_map[old_venue_id] = new_venue_id
    new_venue_id_to_old_map[new_venue_id] = old_venue_id

In [117]:
paper_venue_paper_paper =[]
paper_venue_paper_venue =[]
for k,v in new_core_paper_nodes.items():
    paper_venue_paper_paper.append(k)
    paper_venue_paper_venue.append(old_venue_id_to_new_map[v['features']['Venue']])

In [119]:
len(paper_venue_paper_venue)

12065

In [ ]:
new_core_paper_nodes

In [120]:
data_dict = {
    ('author', 'author-paper', 'paper'): (torch.tensor(author_write_paper_author), torch.tensor(author_write_paper_paper)),
    ('paper', 'cite', 'paper'): (torch.tensor(paper_cite_reference_paper), torch.tensor(paper_cite_reference_reference)),
    ('paper', 'paper-author', 'author'): (torch.tensor(author_write_paper_paper), torch.tensor(author_write_paper_author)),
    ('paper', 'paper-venue', 'venue'): (torch.tensor(paper_venue_paper_paper), torch.tensor(paper_venue_paper_venue)),
    ('venue', 'venue-paper', 'paper'):(torch.tensor(paper_venue_paper_venue), torch.tensor(paper_venue_paper_paper)),
}

In [121]:
g = dgl.heterograph(data_dict)
g

Graph(num_nodes={'author': 35751, 'paper': 12065, 'venue': 2244},
      num_edges={('author', 'author-paper', 'paper'): 95996, ('paper', 'cite', 'paper'): 28561, ('paper', 'paper-author', 'author'): 95996, ('paper', 'paper-venue', 'venue'): 12065, ('venue', 'venue-paper', 'paper'): 12065},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'paper', 'cite'), ('paper', 'author', 'paper-author'), ('paper', 'venue', 'paper-venue'), ('venue', 'paper', 'venue-paper')])

In [123]:
from dgl.data.utils import save_graphs
save_graphs('tkg_dgl.bin',g)

In [1]:
# from dgl.data.utils import load_graphs
# g_for_dw = load_graphs('tkg_dgl.bin')

/data/jx4237data/python_envs/openhgnn/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [7]:
type(g_for_dw[0][0])

dgl.heterograph.DGLGraph

In [24]:
g_for_dw[0][0]

Graph(num_nodes={'author': 35751, 'paper': 12065, 'venue': 2244},
      num_edges={('author', 'author-paper', 'paper'): 95996, ('paper', 'cite', 'paper'): 28561, ('paper', 'paper-author', 'author'): 95996, ('paper', 'paper-venue', 'venue'): 12065, ('venue', 'venue-paper', 'paper'): 12065},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'paper', 'cite'), ('paper', 'author', 'paper-author'), ('paper', 'venue', 'paper-venue'), ('venue', 'paper', 'venue-paper')])

metapath2vec

In [203]:
import torch
import dgl
from torch.optim import SparseAdam
from torch.utils.data import DataLoader
from dgl.nn.pytorch import MetaPath2Vec

model = MetaPath2Vec(g, emb_dim=128, window_size=1,metapath=['author-paper', 'cite', 'paper-venue', 'venue-paper','paper-author'])

  1%|▏         | 504/35751 [00:00<00:13, 2523.85it/s]

100%|██████████| 35751/35751 [00:13<00:00, 2595.63it/s]


In [204]:
dataloader = DataLoader(torch.arange(g.num_nodes('author')), batch_size=128,
                        shuffle=True, collate_fn=model.sample)
optimizer = SparseAdam(model.parameters(), lr=0.025)

In [205]:
from tqdm import tqdm
for (pos_u, pos_v, neg_v) in tqdm(dataloader):
    loss = model(pos_u, pos_v, neg_v)
    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

100%|██████████| 280/280 [00:03<00:00, 75.75it/s]


In [213]:
g.node_attr_schemes('venue')

{'dw_embedding': Scheme(shape=(128,), dtype=torch.float32)}

In [212]:
author_nids = torch.LongTensor(model.local_to_global_nid['venue'])
g.nodes['venue'].data['dw_embedding'] = model.node_embed(author_nids)

In [71]:
from dgl.data.utils import save_graphs
save_graphs('tkg_dgl.bin',g_for_dw[0][0])

In [72]:
from dgl.data.utils import load_graphs
g = load_graphs('tkg_dgl.bin')

In [2]:
g[0][0].node_attr_schemes('venue')

{'dw_embedding': Scheme(shape=(768,), dtype=torch.float32)}

In [50]:
import json


import os
from tqdm import tqdm
import numpy as np

save_dir = '/data/jx4237data/TKG/new_TKG/TKG_new_BAI/embeddings/'

# Function to load a single npz file
def load_npz_file(file_path):
    with np.load(file_path) as data:
        embeddings = data['embeddings']
        ids = data['ids']
    return embeddings, ids

# Function to load all npz files in a directory
def load_all_embeddings(save_dir):
    all_embeddings = []
    all_ids = []
    
    # List all npz files in the directory
    npz_files = [file for file in os.listdir(save_dir) if file.endswith('all.npz')]
    
    for file in npz_files:
        file_path = os.path.join(save_dir, file)
        embeddings, ids = load_npz_file(file_path)
        all_embeddings.append(embeddings)
        all_ids.append(ids)
    
    # Concatenate all embeddings and ids
    all_embeddings = np.concatenate(all_embeddings, axis=0)
    all_ids = np.concatenate(all_ids, axis=0)
    
    return all_embeddings, all_ids

# Load all embeddings and ids
embeddings, ids = load_all_embeddings(save_dir)
print("Loaded embeddings shape:", embeddings.shape)
print("Loaded ids shape:", ids.shape)

Loaded embeddings shape: (1792034, 768)
Loaded ids shape: (1792034,)


In [56]:
embeddings = torch.tensor(embeddings)
embedding_dict = {id_: embedding for id_, embedding in zip(ids, embeddings)}

/tmp/ipykernel_3366676/1098574211.py:1: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  embeddings = torch.tensor(embeddings)


In [64]:
# old_paper_id_to_new_map
# paper_ebd = {}
# for k in embedding_dict:
#     if k in old_paper_id_to_new_map:
#         paper_ebd[old_paper_id_to_new_map[k]] = embedding_dict[k]

In [68]:
del paper_nodes, embedding_dict,embeddings

In [76]:
# # Convert tensors to lists
# paper_ebd_serializable = {
#     key: value.numpy().tolist() for key, value in paper_ebd.items()
# }

# with open('paper_ebd.json', 'w') as json_file:
#     json.dump(paper_ebd_serializable, json_file)

In [217]:
import json
import torch
with open('paper_ebd.json', 'r') as json_file:
    paper_ebd_serializable = json.load(json_file)

# Convert lists back to tensors
paper_ebd = {
    int(key): torch.tensor(value) for key, value in paper_ebd_serializable.items()
}

In [218]:
import json
import torch
from sklearn.decomposition import PCA
import numpy as np

# Load your data
with open('paper_ebd.json', 'r') as json_file:
    paper_ebd_serializable = json.load(json_file)

# Convert lists back to tensors
paper_ebd = {
    int(key): torch.tensor(value) for key, value in paper_ebd_serializable.items()
}

# Extract all embeddings into a single numpy array
embeddings = np.array([value.numpy() for value in paper_ebd.values()])

# Apply PCA to reduce dimensions
pca = PCA(n_components=128)
reduced_embeddings = pca.fit_transform(embeddings)

# Convert back to dictionary format with tensors
reduced_paper_ebd = {
    key: torch.tensor(reduced_embeddings[idx]) for idx, key in enumerate(paper_ebd.keys())
}

In [220]:
ids, embeddings = zip(*[(int(k), v) for k, v in sorted(reduced_paper_ebd.items(), key=lambda x: int(x[0]))])
ids = torch.tensor(ids)
embeddings = torch.stack(embeddings)

In [221]:
embeddings.shape

torch.Size([12065, 128])

In [223]:
g.nodes['paper'].data['abstract'] = embeddings

In [74]:
g[0][0].node_attr_schemes('paper')

{'dw_embedding': Scheme(shape=(768,), dtype=torch.float32),
 'abstract': Scheme(shape=(768,), dtype=torch.float32)}

In [ ]:
g[0][0].nodes['paper'].data['abstract']

In [60]:
g[0][0].nodes['paper'].data['dw_embedding']

Graph(num_nodes={'author': 35751, 'paper': 12065, 'venue': 2244},
      num_edges={('author', 'author-paper', 'paper'): 95996, ('paper', 'cite', 'paper'): 28561, ('paper', 'paper-author', 'author'): 95996, ('paper', 'paper-venue', 'venue'): 12065, ('venue', 'venue-paper', 'paper'): 12065},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'paper', 'cite'), ('paper', 'author', 'paper-author'), ('paper', 'venue', 'paper-venue'), ('venue', 'paper', 'venue-paper')])

In [39]:
g[0][0].nodes('paper')

tensor([    0,     1,     2,  ..., 12062, 12063, 12064])

In [75]:
g = g[0][0]

In [224]:
g

Graph(num_nodes={'author': 35751, 'paper': 12065, 'venue': 2244},
      num_edges={('author', 'author-paper', 'paper'): 95996, ('paper', 'cite', 'paper'): 28561, ('paper', 'paper-author', 'author'): 95996, ('paper', 'paper-venue', 'venue'): 12065, ('venue', 'venue-paper', 'paper'): 12065},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'paper', 'cite'), ('paper', 'author', 'paper-author'), ('paper', 'venue', 'paper-venue'), ('venue', 'paper', 'venue-paper')])

In [228]:
import random

# Number of neighbors to sample
num_papers_per_venue = 5
num_papers_per_author = 3

# Get the paper abstract embeddings
paper_abstracts = g.ndata['abstract']['paper']

# Initialize venue and author abstract embeddings
venue_abstracts = torch.zeros((g.num_nodes('venue'), num_papers_per_venue * 128))
author_abstracts = torch.zeros((g.num_nodes('author'), num_papers_per_author * 128))

# For each venue node
for v in range(g.num_nodes('venue')):
    # Get paper neighbors
    paper_neighbors = g.successors(v, etype='venue-paper')
    # Sample neighbors with replacement
    sampled_papers = random.choices(paper_neighbors.tolist(), k=num_papers_per_venue)
    # Concatenate abstract embeddings
    venue_abstracts[v] = torch.cat([paper_abstracts[p] for p in sampled_papers])

# For each author node
for a in range(g.num_nodes('author')):
    # Get paper neighbors
    paper_neighbors = g.successors(a, etype='author-paper')
    # Sample neighbors with replacement
    sampled_papers = random.choices(paper_neighbors.tolist(), k=num_papers_per_author)
    # Concatenate abstract embeddings
    author_abstracts[a] = torch.cat([paper_abstracts[p] for p in sampled_papers])

# Assign the new embeddings to the graph
g.nodes['venue'].data['abstract'] = venue_abstracts
g.nodes['author'].data['abstract'] = author_abstracts

In [229]:
g.node_attr_schemes('venue')

{'dw_embedding': Scheme(shape=(128,), dtype=torch.float32),
 'abstract': Scheme(shape=(640,), dtype=torch.float32)}

In [230]:
import torch


# Extract existing 'dw_embedding' for paper, venue, and author nodes
paper_embeddings = g.nodes['paper'].data['dw_embedding']
venue_embeddings = g.nodes['venue'].data['dw_embedding']
author_embeddings = g.nodes['author'].data['dw_embedding']

# Initialize new embeddings for paper nodes
venue_aggregated_embeddings = torch.zeros_like(paper_embeddings)
reference_aggregated_embeddings = torch.zeros_like(paper_embeddings)
author_aggregated_embeddings = torch.zeros_like(paper_embeddings)

# Aggregate 'dw_embedding' from neighbor venue nodes
for p in range(g.num_nodes('paper')):
    venue_neighbors = g.successors(p, etype='paper-venue')
    if len(venue_neighbors) > 0:
        venue_aggregated_embeddings[p] = venue_embeddings[venue_neighbors].mean(dim=0)
    else:
        venue_aggregated_embeddings[p] = paper_embeddings[p]

# Aggregate 'dw_embedding' from neighbor paper nodes (through cite relation)
for p in range(g.num_nodes('paper')):
    cited_paper_neighbors = g.successors(p, etype='cite')
    if len(cited_paper_neighbors) > 0:
        reference_aggregated_embeddings[p] = paper_embeddings[cited_paper_neighbors].mean(dim=0)
    else:
        reference_aggregated_embeddings[p] = paper_embeddings[p]

# Aggregate 'dw_embedding' from neighbor author nodes
for p in range(g.num_nodes('paper')):
    author_neighbors = g.successors(p, etype='paper-author')
    if len(author_neighbors) > 0:
        author_aggregated_embeddings[p] = author_embeddings[author_neighbors].mean(dim=0)
    else:
        author_aggregated_embeddings[p] = paper_embeddings[p]

# Assign the new embeddings to the paper nodes in the graph
g.nodes['paper'].data['venue'] = venue_aggregated_embeddings
g.nodes['paper'].data['reference'] = reference_aggregated_embeddings
g.nodes['paper'].data['author'] = author_aggregated_embeddings

In [234]:
g.node_attr_schemes('venue')

{'dw_embedding': Scheme(shape=(128,), dtype=torch.float32),
 'abstract': Scheme(shape=(640,), dtype=torch.float32)}

In [238]:
g.nodes['paper'].data['abstract'].shape

torch.Size([12065, 128])

In [239]:
from dgl.data.utils import save_graphs
save_graphs('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/630deliverable/OpenHGNN/openhgnn/dataset/academic4HetGNN/graph.bin',g)

In [5]:
from dgl.data.utils import load_graphs
g = load_graphs('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/630deliverable/OpenHGNN/openhgnn/dataset/academic4HetGNN/graph.bin')
g = g[0][0]

In [13]:
core_paper_year = {}
for k,v in core_paper_nodes.items():
    core_paper_year[old_paper_id_to_new_map[k]] = v['features']['PubYear']

In [14]:
import pandas as pd
df = pd.DataFrame(list(core_paper_year.items()), columns=['paper_id', 'pub_year'])
df

paper_id  pub_year
0             0      1975
1             1      1975
2             2      1978
3             3      1975
4             4      1975
...         ...       ...
12060     12060      2021
12061     12061      2022
12062     12062      2021
12063     12063      2021
12064     12064      2021

[12065 rows x 2 columns]

In [15]:
n = 2015

# Separate the DataFrame into two based on the year n
before_n_df = df[df['pub_year'] < n]
after_n_df = df[df['pub_year'] >= n]

# Extract the paper IDs from the two DataFrames
before_n_paper_ids = before_n_df['paper_id'].tolist()
after_n_paper_ids = after_n_df['paper_id'].tolist()

print("Paper IDs before year", n, ":", len(before_n_paper_ids))
print("Paper IDs on or after year", n, ":", len(after_n_paper_ids))

Paper IDs before year 2015 : 6417
Paper IDs on or after year 2015 : 5648


In [118]:
g

Graph(num_nodes={'author': 35751, 'paper': 12065, 'venue': 2244},
      num_edges={('author', 'author-paper', 'paper'): 95996, ('paper', 'cite', 'paper'): 28561, ('paper', 'paper-author', 'author'): 95996, ('paper', 'paper-venue', 'venue'): 12065, ('venue', 'venue-paper', 'paper'): 12065},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'paper', 'cite'), ('paper', 'author', 'paper-author'), ('paper', 'venue', 'paper-venue'), ('venue', 'paper', 'venue-paper')])

tensor([22289,    25,  5220])

In [16]:
from itertools import combinations
for pair in combinations(g.successors(50, etype='paper-author').tolist(), 2):
    print(tuple(sorted(pair)))

(25, 22289)
(5220, 22289)
(25, 5220)


In [18]:
import random
import numpy as np
from itertools import combinations

# Helper function to get author pairs for given paper ids
def get_author_pairs(paper_ids):
    author_pairs = set()
    for paper_id in paper_ids:
        authors = g.predecessors(paper_id, etype='author-paper')
        for pair in combinations(authors.tolist(), 2):
            author_pairs.add(tuple(sorted(pair)))
    return author_pairs

# Get author collaborations before and after 2015
before_2015_pairs = get_author_pairs(before_n_paper_ids)
after_2015_pairs = get_author_pairs(after_n_paper_ids)


def get_author_pairs(paper_ids):
    author_pairs = set()
    for paper_id in paper_ids:
        authors = g.predecessors(paper_id, etype='author-paper')
        for pair in combinations(authors.tolist(), 2):
            author_pairs.add(tuple(sorted(pair)))
    return author_pairs

# Get author collaborations before and after 2015
before_2015_pairs = get_author_pairs(before_n_paper_ids)
after_2015_pairs = get_author_pairs(after_n_paper_ids)

# Get all author ids
all_authors = list(range(g.num_nodes('author')))

# Function to generate samples
def generate_samples(author_pairs, all_authors, existing_pairs):
    samples = []
    new_pairs = set()
    for pair in author_pairs:
        samples.append((pair[0], pair[1], 1))
        # Find a negative sample with a common author
        i, j = pair
        negative_sample = None
        while True:
            k = random.choice(all_authors)
            if k != i and k != j and (i, k) not in existing_pairs and (k, i) not in existing_pairs and (i, k) not in new_pairs and (k, i) not in new_pairs:
                negative_sample = (i, k, 0)
                new_pairs.add((i, k))
                break
        samples.append(negative_sample)
    # Add new pairs to existing pairs after iteration
    existing_pairs.update(new_pairs)
    return samples

# Generate training data
train_samples = generate_samples(before_2015_pairs, all_authors, existing_pairs=before_2015_pairs.copy())

# Filter new collaborations for test data
new_collaborations = after_2015_pairs - before_2015_pairs
test_samples = generate_samples(new_collaborations, all_authors, existing_pairs= after_2015_pairs.copy() | before_2015_pairs.copy())

# Write to files
def write_to_file(filename, samples):
    with open(filename, 'w') as f:
        for sample in samples:
            f.write(f"{sample[0]}, {sample[1]}, {sample[2]}\n")

write_to_file('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/630deliverable/OpenHGNN/openhgnn/dataset/academic4HetGNN/a_a_list_train_2015_modified.txt', train_samples)
write_to_file('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/630deliverable/OpenHGNN/openhgnn/dataset/academic4HetGNN/a_a_list_test_2015_modified.txt', test_samples)

In [245]:
g.etypes

['author-paper', 'cite', 'paper-author', 'paper-venue', 'venue-paper']

# change to d = 128

In [227]:
g.node_attr_schemes('paper')

{'dw_embedding': Scheme(shape=(128,), dtype=torch.float32),
 'abstract': Scheme(shape=(128,), dtype=torch.float32)}

In [ ]:
g.nodes['paper'].data.pop('author', None)

# give paper a category label (from semantic scholar)

In [16]:
pmids = set(list(core_paper_nodes.keys()))

In [5]:
import pickle
papers= pickle.load(open('/data/jx4237data/TKG/new_TKG/Bridge2AI_s2_paper_results.pkl','rb'))

In [7]:
papers[0]

{'paperId': '9cac1c470cc202695fce793a4e804a43790cf224', 'externalIds': {'MAG': '2526413677', 'DOI': '10.1038/nmeth.4000', 'CorpusId': 3545216, 'PubMed': '27684579'}, 'corpusId': 3545216, 'title': 'DoCM: a database of curated mutations in cancer', 'abstract': None, 'venue': 'Nature Methods', 'year': 2016, 'referenceCount': 9, 'citationCount': 91, 'fieldsOfStudy': ['Biology', 'Medicine'], 's2FieldsOfStudy': [{'category': 'Biology', 'source': 'external'}, {'category': 'Medicine', 'source': 'external'}, {'category': 'Biology', 'source': 's2-fos-model'}, {'category': 'Computer Science', 'source': 's2-fos-model'}, {'category': 'Medicine', 'source': 's2-fos-model'}], 'publicationTypes': ['LettersAndComments'], 'publicationDate': '2016-09-29', 'journal': {'name': 'Nature Methods', 'pages': '806-807', 'volume': '13'}, 'citationStyles': {'bibtex': '@Article{Ainscough2016DoCMAD,\n author = {Benjamin J. Ainscough and M. Griffith and Adam C. Coffman and A. Wagner and J. Kunisaki and Mayank N. K. Ch

In [6]:
corepaper_fields = {}
for paper in papers:
    if 'PubMed' in paper['externalIds']:
        if paper['externalIds']['PubMed'] in pmids:
            corepaper_fields[paper['externalIds']['PubMed']] = paper['fieldsOfStudy']


In [7]:
from collections import Counter
subject_counter = Counter()
for k, v in corepaper_fields.items():
    subject_counter.update(v)

In [10]:
subject_counter

Counter({'Biology': 2104,
         'Medicine': 8102,
         'Computer Science': 1992,
         'Psychology': 405,
         'Materials Science': 39,
         'Business': 60,
         'Physics': 50,
         'Sociology': 37,
         'Chemistry': 227,
         'Geography': 18,
         'Mathematics': 92,
         'Engineering': 57,
         'Political Science': 37,
         'Philosophy': 3,
         'Art': 2,
         'Economics': 6,
         'History': 3,
         'Environmental Science': 2,
         'Geology': 2})

In [11]:
preference_order = ['Others', 'Computer Science', 'Biology', 'Medicine']

# Function to assign a single label based on the preference order
def assign_single_label(labels):
    # Define the categories
    categories = ['Computer Science', 'Biology', 'Medicine']
    # Convert labels to the 4 categories
    converted_labels = {label if label in categories else 'Others' for label in labels}
    # Apply the preference order
    for pref in preference_order:
        if pref in converted_labels:
            return pref

# Assign single labels to each paper
single_labels = {paper_id: assign_single_label(labels) for paper_id, labels in corepaper_fields.items()}
single_labels

{'27684579': 'Biology',
 '25825871': 'Biology',
 '31552413': 'Computer Science',
 '10648846': 'Computer Science',
 '33589700': 'Computer Science',
 '19632506': 'Medicine',
 '16685884': 'Computer Science',
 '27742616': 'Medicine',
 '16387212': 'Medicine',
 '30550789': 'Biology',
 '31750926': 'Computer Science',
 '11604731': 'Computer Science',
 '31288129': 'Biology',
 '25727506': 'Medicine',
 '27664130': 'Computer Science',
 '29606589': 'Biology',
 '15180333': 'Medicine',
 '34087201': 'Medicine',
 '30216330': 'Medicine',
 '21346986': 'Medicine',
 '28594152': 'Medicine',
 '17020965': 'Biology',
 '24564913': 'Biology',
 '34427681': 'Medicine',
 '32790539': 'Medicine',
 '33384883': 'Medicine',
 '19811689': 'Computer Science',
 '33232313': 'Computer Science',
 '28583177': 'Computer Science',
 '22072698': 'Others',
 '16912648': 'Medicine',
 '23949796': 'Biology',
 '26996340': 'Medicine',
 '24799088': 'Computer Science',
 '31313047': 'Medicine',
 '25924931': 'Computer Science',
 '28198142': '

In [14]:
Counter(single_labels.values())

Counter({'Biology': 1757,
         'Computer Science': 1819,
         'Medicine': 3516,
         'Others': 1015})

# let us do acm4NSHE similar graph

tkg to acm4gtn: venue to subject.

In [15]:
from dgl.data.utils import load_graphs
gns, _ = load_graphs('/data/jx4237data/TKG/new_TKG/TKG_new_BAI/630deliverable/OpenHGNN/openhgnn/dataset/acm4NSHE/graph.bin')

/data/jx4237data/python_envs/openhgnn/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [14]:
gns

[Graph(num_nodes={'author': 7167, 'paper': 4019, 'subject': 60},
       num_edges={('author', 'author-paper', 'paper'): 13407, ('paper', 'paper-author', 'author'): 13407, ('paper', 'paper-subject', 'subject'): 4019, ('subject', 'subject-paper', 'paper'): 4019},
       metagraph=[('author', 'paper', 'author-paper'), ('paper', 'author', 'paper-author'), ('paper', 'subject', 'paper-subject'), ('subject', 'paper', 'subject-paper')])]

In [15]:
g[0].node_attr_schemes('paper')

NameError: name 'g' is not defined

In [ ]:
import numpy as np
np.array(g[0].nodes['paper'].data['label']).tolist

Counter({2: 1061, 1: 965, 0: 1993})

In [16]:
len(pmids)

12065

In [17]:
len(single_labels)

8107

In [18]:
single_labels

{'27684579': 'Biology',
 '25825871': 'Biology',
 '31552413': 'Computer Science',
 '10648846': 'Computer Science',
 '33589700': 'Computer Science',
 '19632506': 'Medicine',
 '16685884': 'Computer Science',
 '27742616': 'Medicine',
 '16387212': 'Medicine',
 '30550789': 'Biology',
 '31750926': 'Computer Science',
 '11604731': 'Computer Science',
 '31288129': 'Biology',
 '25727506': 'Medicine',
 '27664130': 'Computer Science',
 '29606589': 'Biology',
 '15180333': 'Medicine',
 '34087201': 'Medicine',
 '30216330': 'Medicine',
 '21346986': 'Medicine',
 '28594152': 'Medicine',
 '17020965': 'Biology',
 '24564913': 'Biology',
 '34427681': 'Medicine',
 '32790539': 'Medicine',
 '33384883': 'Medicine',
 '19811689': 'Computer Science',
 '33232313': 'Computer Science',
 '28583177': 'Computer Science',
 '22072698': 'Others',
 '16912648': 'Medicine',
 '23949796': 'Biology',
 '26996340': 'Medicine',
 '24799088': 'Computer Science',
 '31313047': 'Medicine',
 '25924931': 'Computer Science',
 '28198142': '

In [18]:
# Dictionaries to store the mappings with paper_id in their names
old_paper_id_to_new_acm_map = {}
new_acm_paper_id_to_old_map = {}

# Iterate over the dictionary and create the mappings
for new_paper_id, old_paper_id in enumerate(single_labels):
    old_paper_id_to_new_acm_map[old_paper_id] = new_paper_id
    new_acm_paper_id_to_old_map[new_paper_id] = old_paper_id

# Create the new dictionary with the new keys
new_acm_core_paper_nodes = {new_paper_id: core_paper_nodes[old_paper_id] for old_paper_id, new_paper_id in old_paper_id_to_new_acm_map.items()}

In [19]:
len(new_acm_core_paper_nodes)

8107

In [20]:
del paper_nodes

In [23]:
new_author_set = set()
for k,v in new_acm_core_paper_nodes.items():
    for old_author in v['neighbors']['author']:
        new_author_set.add(old_author)

In [26]:
new_author_list = list(new_author_set)

In [27]:
old_author_id_to_new_acm_map = {}
new_acm_author_id_to_old_map = {}

# Iterate over the dictionary and create the mappings
for new_author_id, old_author_id in enumerate(new_author_list):
    old_author_id_to_new_acm_map[old_author_id] = new_author_id
    new_acm_author_id_to_old_map[new_author_id] = old_author_id

Let's Create!

In [28]:
import dgl
import torch

In [29]:
# data_dict = {
#     ('author', 'author-paper', 'paper'): (torch.tensor(author_write_paper_author), torch.tensor(author_write_paper_paper)),
#     ('paper', 'paper-author', 'author'): (torch.tensor(author_write_paper_paper), torch.tensor(author_write_paper_author)),
#     ('paper', 'paper-subject', 'subject'): (torch.tensor(paper_venue_paper_paper), torch.tensor(paper_venue_paper_venue)),
#     ('subject', 'subject-paper', 'paper'):(torch.tensor(paper_venue_paper_venue), torch.tensor(paper_venue_paper_paper)),
# }

NameError: name 'author_write_paper_author' is not defined

In [30]:
author_write_paper_author = []
author_write_paper_paper = []
for k,v in new_acm_core_paper_nodes.items():
    for old_author_id in v['neighbors']['author'].keys():
        author_write_paper_paper.append(k)
        author_write_paper_author.append(old_author_id_to_new_acm_map[old_author_id])

In [31]:
venue_set = set()
for k,v in new_acm_core_paper_nodes.items():
    venue_set.update([v['features']['Venue']])

In [32]:
venue_list = list(venue_set)
old_venue_id_to_new_acm_map = {}
new_acm_venue_id_to_old_map = {}

# Iterate over the list and create the mappings
for new_venue_id, old_venue_id in enumerate(venue_list):
    old_venue_id_to_new_acm_map[old_venue_id] = new_venue_id
    new_acm_venue_id_to_old_map[new_venue_id] = old_venue_id

In [33]:
paper_venue_paper_paper =[]
paper_venue_paper_venue =[]
for k,v in new_acm_core_paper_nodes.items():
    paper_venue_paper_paper.append(k)
    paper_venue_paper_venue.append(old_venue_id_to_new_acm_map[v['features']['Venue']])

In [34]:
len(paper_venue_paper_venue)

8107

In [35]:
new_acm_core_paper_nodes

{0: {'features': {'AuthorNum': 11,
   'PubYear': 2016,
   'CitedCount': 49,
   'Title': 'DoCM: a database of curated mutations in cancer.',
   'Abstract': '',
   'Venue': 'Nature methods',
   'is_core': 1},
  'neighbors': {'author': {'13583650': [1,
     ' Siteman Cancer Center, Washington University School of Medicine St Louis, Missouri, USA united states of america====='],
    '3784209': [2,
     'Department of Genetics Washington University School of Medicine St Louis, Missouri, USA united states of america====='],
    '6146329': [3,
     'McDonnell Genome Institute McDonnell Genome Institute, Washington University School of Medicine St Louis, Missouri, USA united states of america====='],
    '13449777': [4,
     ' Siteman Cancer Center, Washington University School of Medicine St Louis, Missouri, USA united states of america====='],
    '7872292': [5,
     'McDonnell Genome Institute McDonnell Genome Institute, Washington University School of Medicine St Louis, Missouri, USA unite

In [36]:
data_dict = {
    ('author', 'author-paper', 'paper'): (torch.tensor(author_write_paper_author), torch.tensor(author_write_paper_paper)),
    ('paper', 'paper-author', 'author'): (torch.tensor(author_write_paper_paper), torch.tensor(author_write_paper_author)),
    ('paper', 'paper-subject', 'subject'): (torch.tensor(paper_venue_paper_paper), torch.tensor(paper_venue_paper_venue)),
    ('subject', 'subject-paper', 'paper'):(torch.tensor(paper_venue_paper_venue), torch.tensor(paper_venue_paper_paper)),
}

In [37]:
g = dgl.heterograph(data_dict)
g

Graph(num_nodes={'author': 35750, 'paper': 8107, 'subject': 1703},
      num_edges={('author', 'author-paper', 'paper'): 79558, ('paper', 'paper-author', 'author'): 79558, ('paper', 'paper-subject', 'subject'): 8107, ('subject', 'subject-paper', 'paper'): 8107},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'author', 'paper-author'), ('paper', 'subject', 'paper-subject'), ('subject', 'paper', 'subject-paper')])

In [38]:
gns

[Graph(num_nodes={'author': 7167, 'paper': 4019, 'subject': 60},
       num_edges={('author', 'author-paper', 'paper'): 13407, ('paper', 'paper-author', 'author'): 13407, ('paper', 'paper-subject', 'subject'): 4019, ('subject', 'subject-paper', 'paper'): 4019},
       metagraph=[('author', 'paper', 'author-paper'), ('paper', 'author', 'paper-author'), ('paper', 'subject', 'paper-subject'), ('subject', 'paper', 'subject-paper')])]

In [39]:
gns[0].node_attr_schemes('paper')

{'label': Scheme(shape=(), dtype=torch.int64),
 'h': Scheme(shape=(128,), dtype=torch.float32)}

In [40]:
gns[0].nodes['paper'].data['label']

tensor([2, 2, 2,  ..., 2, 2, 2])

In [41]:
g

Graph(num_nodes={'author': 35750, 'paper': 8107, 'subject': 1703},
      num_edges={('author', 'author-paper', 'paper'): 79558, ('paper', 'paper-author', 'author'): 79558, ('paper', 'paper-subject', 'subject'): 8107, ('subject', 'subject-paper', 'paper'): 8107},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'author', 'paper-author'), ('paper', 'subject', 'paper-subject'), ('subject', 'paper', 'subject-paper')])

In [42]:
field2label = {'Biology':0, 'Computer Science':1, 'Medicine':2, 'Others':3}

In [43]:
import torch
torch.tensor(list({old_paper_id_to_new_acm_map[k]: field2label[v] for k,v in single_labels.items()}.values())).shape

torch.Size([8107])

In [44]:
g.nodes['paper'].data['label'] = torch.tensor(list({old_paper_id_to_new_acm_map[k]: field2label[v] for k,v in single_labels.items()}.values()))

In [45]:
g.node_attr_schemes('paper')

{'label': Scheme(shape=(), dtype=torch.int64)}

In [46]:
g.nodes['paper'].data['label']

tensor([0, 0, 1,  ..., 1, 0, 3])

In [47]:
g

Graph(num_nodes={'author': 35750, 'paper': 8107, 'subject': 1703},
      num_edges={('author', 'author-paper', 'paper'): 79558, ('paper', 'paper-author', 'author'): 79558, ('paper', 'paper-subject', 'subject'): 8107, ('subject', 'subject-paper', 'paper'): 8107},
      metagraph=[('author', 'paper', 'author-paper'), ('paper', 'author', 'paper-author'), ('paper', 'subject', 'paper-subject'), ('subject', 'paper', 'subject-paper')])

In [48]:
import torch
import dgl
from torch.optim import SparseAdam
from torch.utils.data import DataLoader
from dgl.nn.pytorch import MetaPath2Vec

model = MetaPath2Vec(g, emb_dim=128, window_size=1,metapath=['author-paper', 'paper-subject', 'subject-paper','paper-author'])

 16%|█▌        | 5696/35750 [00:02<00:10, 2783.63it/s]

100%|██████████| 35750/35750 [00:12<00:00, 2816.29it/s]


In [49]:
dataloader = DataLoader(torch.arange(g.num_nodes('author')), batch_size=128,
                        shuffle=True, collate_fn=model.sample)
optimizer = SparseAdam(model.parameters(), lr=0.025)

: 

In [50]:
from tqdm import tqdm
for (pos_u, pos_v, neg_v) in tqdm(dataloader):
    loss = model(pos_u, pos_v, neg_v)
    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

  0%|          | 0/280 [00:00<?, ?it/s]

In [ ]:
g.node_attr_schemes('venue')

{'dw_embedding': Scheme(shape=(128,), dtype=torch.float32)}

In [ ]:
author_nids = torch.LongTensor(model.local_to_global_nid['venue'])
g.nodes['venue'].data['dw_embedding'] = model.node_embed(author_nids)

In [ ]:
from dgl.data.utils import save_graphs
save_graphs('tkg_dgl.bin',g_for_dw[0][0])

In [ ]:
from dgl.data.utils import load_graphs
g = load_graphs('tkg_dgl.bin')

In [ ]:
g[0][0].node_attr_schemes('venue')

{'dw_embedding': Scheme(shape=(768,), dtype=torch.float32)}